<a href="https://colab.research.google.com/github/itsdivya1309/Machine-Learning/blob/main/LLMs/Text%20Clustering%20and%20Topic%20Modeling/Topic_Modeling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Topic Modeling

**Topic Modeling**: finding themes or latent topics in a collection of textual data. Traditionally, it invlovles finding a collection of keywords or phrases that best represent and capture the meaning of the topic.

## Arxive's Articles

We will try to find topics of the Arxive articles from the 9 categories listed below:

- 'q-bio.BM': 'Biomolecules',
- 'q-bio.CB': 'Cell Behavior',
- 'q-bio.GN': 'Genomics',
- 'q-bio.MN': 'Molecular Networks',
- 'q-bio.NC': 'Neurons and Cognition',
- 'q-bio.OT': 'Other Quantitative Biology',
- 'q-bio.PE': 'Populations and Evolution',
- 'q-bio.QM': 'Quantitative Methods',
- 'q-bio.SC': 'Subcellular Processes',
- 'q-bio.TO': 'Tissues and Organs',

In [ ]:
! pip install kaggle
! mkdir ~/.kaggle
! cp kaggle.json ~/.kaggle/
! chmod 600 ~/.kaggle/kaggle.json

In [ ]:
!kaggle datasets download -d Cornell-University/arxiv

Dataset URL: https://www.kaggle.com/datasets/Cornell-University/arxiv
License(s): CC0-1.0
 99% 1.40G/1.40G [00:21<00:00, 63.3MB/s]
100% 1.40G/1.40G [00:21<00:00, 70.3MB/s]


In [ ]:
!unzip arxiv.zip -d arxiv_data

Archive:  arxiv.zip
  inflating: arxiv_data/arxiv-metadata-oai-snapshot.json  


In [ ]:
import numpy as np
import pandas as pd

In [ ]:
import json

# Load JSON file
json_file = "arxiv_data/arxiv-metadata-oai-snapshot.json"

# The categories of interest
bio_categories = {
    'q-bio.BM', 'q-bio.CB', 'q-bio.GN', 'q-bio.MN',
    'q-bio.NC', 'q-bio.OT', 'q-bio.PE', 'q-bio.QM', 'q-bio.SC'
}

# Prepare a list to store filtered data
filtered_data = []

# Process the file line by line
with open(json_file, "r") as f:
    for line in f:
        paper = json.loads(line)  # Parse JSON line

        # Check if any category in the paper matches our target categories
        if any(cat in paper['categories'] for cat in bio_categories):
            # Extract only the required fields
            filtered_data.append({
                "title": paper.get("title", ""),
                "authors": paper.get("authors", ""),
                "abstract": paper.get("abstract", ""),
                "doi": paper.get("doi", "N/A")  # Default to "N/A" if DOI is missing
            })

In [ ]:
# Convert to a DataFrame
papers = pd.DataFrame(filtered_data)

# Display the first few rows
papers.head()

title  \
0  Molecular Synchronization Waves in Arrays of A...   
1  Origin of adaptive mutants: a quantum measurem...   
2  A remark on the number of steady states in a m...   
3           Complexities of Human Promoter Sequences   
4  Intricate Knots in Proteins: Function and Evol...   

                                             authors  \
0  Vanessa Casagrande, Yuichi Togashi, Alexander ...   
1                                     Vasily Ogryzko   
2                  Liming Wang and Eduardo D. Sontag   
3       Fangcui Zhao, Huijie Yang, and Binghong Wang   
4  Peter Virnau (1), Leonid A. Mirny (1,2), Mehra...   

                                            abstract  \
0    Spatiotemporal pattern formation in a produc...   
1    This is a supplement to the paper arXiv:q-bi...   
2    The multisite phosphorylation-dephosphorylat...   
3    By means of the diffusion entropy approach, ...   
4    A number of recently discovered protein stru...   

                             doi  
0  10.1103/PhysRevLett.99.048301  
1                           None  
2                           None  
3     10.1016/j.jtbi.2007.03.035  
4                           None

In [ ]:
# Extract metadata
abstracts = papers['abstract']
titles = papers['title']
abstracts.shape

(45847,)

## BERTopic: a Modular Topic Modelling Framework

BERTopic is a topic modeling technique that leverages clusters of semantically similar texts to extract various types of topic repesentations.

It essentially has two components:

1. **Text Clustering**
    * Embed the documents using sentence transformer or any other embedding model.
    * Reduce the size of embeddings using any dimensionality reduction technique.
    * Cluster the reduced embeddings into semantically similar groups.

    ```
    SBERT -----> UMAP -----> HDBSCAN
    ```

2. **Topic Modeling**
    * The second part of BERTopic's pipeline is representing the topics: the calculation of the weight of a term `x` in a class `c`.
    * In topic modeling, we calculate the frequency of words in the entire cluster instead of only one document.
    * Each cluster is treated as a single document and `class-based TF-IDF (c-TF-IDF)` is calculated for each word, which gives more importance to contextual words and less weightage to common/stop words.

    ```
    CountVectorizer -----> c-TF-IDF
    ```

In [ ]:
# Embedding model
from sentence_transformers import SentenceTransformer

embedding_model = SentenceTransformer("thenlper/gte-small")

embeddings = embedding_model.encode(abstracts, show_progress_bar=True)
print(embeddings.shape)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/385 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/68.1k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/57.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/583 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

1_Pooling%2Fconfig.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Batches:   0%|          | 0/1433 [00:00<?, ?it/s]

(45847, 384)


In [ ]:
! pip install bertopic

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.7/143.7 kB 10.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 68.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 81.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 57.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 1.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 15.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 53.2 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstall

### Using BERTopic with default models

In [ ]:
! pip install umap-learn

In [ ]:
import umap

# UMAP model to reduce 384 dimensions to 9
umap_model = umap.UMAP(n_components=9, min_dist=0.1, metric='cosine', random_state=42)

# Fit and transform the embeddings
reduced_embeddings = umap_model.fit_transform(embeddings)

/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/umap/umap_.py:1952: UserWarning: n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.
  warn(


In [ ]:
# Form clusters using HDBSCAN
from sklearn.cluster import HDBSCAN

hdbscan_model = HDBSCAN(min_cluster_size=60, metric='euclidean', cluster_selection_method='eom')

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer_model = CountVectorizer(stop_words="english", min_df=2, ngram_range=(1, 2))

In [ ]:
from bertopic import BERTopic

# Train our model with our previously defined models
topic_model = BERTopic(
    embedding_model=embedding_model,
    umap_model=umap_model,
    hdbscan_model=hdbscan_model,
    vectorizer_model=vectorizer_model,
    verbose=True)
topic_model.fit(abstracts, reduced_embeddings)

2025-03-04 13:37:40,619 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2025-03-04 13:40:54,364 - BERTopic - Dimensionality - Completed ✓
2025-03-04 13:40:54,367 - BERTopic - Cluster - Start clustering the reduced embeddings
2025-03-04 13:41:26,343 - BERTopic - Cluster - Completed ✓
2025-03-04 13:41:26,355 - BERTopic - Representation - Extracting topics from clusters using representation models.
2025-03-04 13:41:48,064 - BERTopic - Representation - Completed ✓


In [ ]:
topic_model.get_topic_info()

Topic  Count                                               Name  \
0      -1    427                  -1_model_protein_vaccination_drug   
1       0  25847                         0_data_model_brain_network   
2       1   2937                  1_tree_species_phylogenetic_trees   
3       2   1264                 2_population_species_prey_predator   
4       3   1144                       3_covid_19_covid 19_pandemic   
5       4    882                4_protein_molecular_prediction_drug   
6       5    847                  5_folding_protein_proteins_energy   
7       6    812              6_cooperation_game_games_evolutionary   
8       7    781                 7_protein_molecules_molecular_drug   
9       8    781                    8_species_population_model_fish   
10      9    692                 9_species_population_model_process   
11     10    621                             10_ms_ion_mass_protein   
12     11    584         11_epidemic_infected_susceptible_infection   
13     12    570               12_protein_proteins_energy_molecular   
14     13    464               13_quantum_resistance_evolution_gene   
15     14    459                    14_dengue_hiv_infection_disease   
16     15    457                    15_protein_docking_structure_3d   
17     16    441          16_cultural_creativity_evolution_creative   
18     17    424                17_rna_structures_structure_protein   
19     18    391                         18_dna_chain_force_polymer   
20     19    368                      19_covid 19_covid_19_pandemic   
21     20    323                 20_immune_cells_repertoire_antigen   
22     21    312                        21_cryo_cryo em_em_electron   
23     22    305           22_quantum_evolution_brain_consciousness   
24     23    281              23_dna_phase_phase separation_amyloid   
25     24    271              24_epidemic_disease_vaccination_ebola   
26     25    225         25_epidemic_disease_infectious_individuals   
27     26    214                   26_malaria_immune_host_infection   
28     27    191  27_population_fixation_species_fixation probab...   
29     28    184                           28_covid_covid 19_19_cov   
30     29    182                  29_drug_ribosome_translation_mrna   
31     30    180                             30_hla_tcr_host_immune   
32     31    162                      31_crispr_drug_cas_crispr cas   
33     32    154          32_influenza_vaccination_epidemic_disease   
34     33    139                33_drug_ddi_drugs_drug combinations   
35     34    139              34_vaccination_vaccine_epidemic_covid   
36     35    131           35_protein_proteins_allosteric_molecular   
37     36    121     36_quantum_persistent_drug_persistent homology   
38     37    118                        37_dna_prion_bubble_melting   
39     38    113               38_epidemic_disease_model_infectious   
40     39    106                    39_protein_proteins_folding_dna   
41     40    104               40_epidemic_disease_model_infectious   
42     41    100         41_radical_channels_radical pair_transport   
43     42     97                 42_energy_protein_folding_proteins   
44     43     94                 43_protein_sequence_prediction_rna   
45     44     91                 44_capsid_assembly_capsids_viruses   
46     45     89                     45_strategies_zd_player_payoff   
47     46     88              46_social_cooperation_group_selection   
48     47     75                 47_protein_energy_folding_proteins   
49     48     65             48_protein_structures_amyloid_proteins   

                                       Representation  \
0   [model, protein, vaccination, drug, disease, e...   
1   [data, model, brain, network, networks, cell, ...   
2   [tree, species, phylogenetic, trees, fitness, ...   
3   [population, species, prey, predator, model, e...   
4   [covid, 19, covid 19, pandemic, cov, sars, sar...   
5   [protein, molecular, prediction, dru

In [ ]:
topic_model.get_topic(48)

[('protein', 0.025490549007796955),
 ('structures', 0.0177940824125552),
 ('amyloid', 0.016970138543439515),
 ('proteins', 0.015194229722274665),
 ('molecular', 0.015018478010263639),
 ('structure', 0.013633411786610398),
 ('amyloidogenic', 0.013425275131773912),
 ('dna', 0.01308861346705917),
 ('rna', 0.012702318934897011),
 ('target', 0.011855808711827315)]

In [ ]:
# Visualize barchart with ranked keywords
topic_model.visualize_barchart(top_n_topics=50)  # Adjust `top_n_topics` as needed

In [ ]:
# Visualize relationships between topics
topic_model.visualize_heatmap(n_clusters=10)

In [ ]:
# Visualize the potential hierarchical structure of topics
topic_model.visualize_hierarchy()

In [ ]:
# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = umap.UMAP(n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [ ]:
fig = topic_model.visualize_documents(
    titles,
    reduced_embeddings=reduced_embeddings,
    width=1200,
    hide_annotations=True)

# Update fonts of legend for easier visualization
fig.update_layout(font=dict(size=16))

In [ ]:
topic_model.visualize_topics()

## Fine-tuning the topic representations

We can fine-tune the topic representiations by reranking the initial distribution of words to improve the representation. The reranker models are called representation models in BERTopic.

We are using two reranker models here:

1. **KeyBERTInspired**
    * Inspired by KeyBERT, a model that extracts keywords from texts by comparing cosine similarity of word and document embeddings.
    * KeyBERTInspired extracts the most representative documents per topic by calculating the similarity between a document's c-TF-IDF values and those of the topic they correspond to.
    * The average document embedding per topic is compared to the embeddings of candidate keywords to rerank the keywords.

2. **Maximal marginal relevance (MMR)**
    * Diversifies our topic representations.
    * Finds a set of keywords that are diverse from one another but still relate to the documents they are compared to.

In [ ]:
# Save original representations
from copy import deepcopy
original_topics = deepcopy(topic_model.topic_representations_)

In [ ]:
def topic_differences(model, original_topics, nr_topics=5):
    """Show the differences in topic representations between two models """
    df = pd.DataFrame(columns=["Topic", "Original", "Updated"])
    for topic in range(nr_topics):
        # Extract top 5 words per topic per model
        og_words = " | ".join(list(zip(*original_topics[topic]))[0][:5])
        new_words = " | ".join(list(zip(*model.get_topic(topic)))[0][:5])
        df.loc[len(df)] = [topic, og_words, new_words]
    return df

In [ ]:
from bertopic.representation import KeyBERTInspired

# Update our topic representations using KeyBERTInspired
representation_model = KeyBERTInspired()
topic_model.update_topics(abstracts, representation_model=representation_model)

In [ ]:
# Show topic differences
topic_differences(topic_model, original_topics)

Topic                                           Original  \
0      0          data | model | brain | network | networks   
1      1    tree | species | phylogenetic | trees | fitness   
2      2     population | species | prey | predator | model   
3      3             covid | 19 | covid 19 | pandemic | cov   
4      4  protein | molecular | prediction | drug | lear...   

                                             Updated  
0            neurons | neural | cells | brain | cell  
1  phylogenetic | evolutionary | evolution | netw...  
2  extinction | dispersal | coexistence | stochas...  
3  epidemic | pandemic | covid | coronavirus | ou...  
4  predicting | proteins | prediction | protein |...

In [ ]:
from bertopic.representation import MaximalMarginalRelevance

# Update our topic representations to MaximalMarginalRelevance
representation_model = MaximalMarginalRelevance(diversity=0.2)
topic_model.update_topics(abstracts, representation_model=representation_model)

In [ ]:
# Show topic differences
topic_differences(topic_model, original_topics)

Topic                                           Original  \
0      0          data | model | brain | network | networks   
1      1    tree | species | phylogenetic | trees | fitness   
2      2     population | species | prey | predator | model   
3      3             covid | 19 | covid 19 | pandemic | cov   
4      4  protein | molecular | prediction | drug | lear...   

                                             Updated  
0                       to | we | for | data | model  
1    tree | species | phylogenetic | trees | fitness  
2  population | species | prey | predator | extin...  
3        covid | pandemic | sars | epidemic | spread  
4  protein | molecular | prediction | learning | ...